In [ ]:
# Resample
from osgeo import gdal, ogr, osr

# Define the paths to your rasters
lidarHAG_path = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\lidarHAG\LIDAR_GEDI_CO.tif"
pcl_path = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\Input\pcl_west_wgs_CO_3.tif"

# Open the source (lidarHAG) and target (pcl) datasets
src_ds = gdal.Open(lidarHAG_path, gdal.GA_ReadOnly)
target_ds = gdal.Open(pcl_path, gdal.GA_ReadOnly)


# Get the Geotransform and Projection from the target dataset
target_transform = target_ds.GetGeoTransform()
target_projection = target_ds.GetProjection()
target_cols = target_ds.RasterXSize
target_rows = target_ds.RasterYSize

# Create a new dataset for output with the same size and projection as the target
driver = gdal.GetDriverByName('GTiff')
output_path = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\Input\Resampled_LIDAR_GEDI_CO_11.tif"
out_ds = driver.Create(output_path, target_cols, target_rows, 1, src_ds.GetRasterBand(1).DataType)
out_ds.SetGeoTransform(target_transform)
out_ds.SetProjection(target_projection)

# Perform the resampling
gdal.ReprojectImage(src_ds, out_ds, src_ds.GetProjection(), target_projection, gdal.GRA_Bilinear)

# Close the datasets
src_ds = None
target_ds = None
out_ds = None

print("Resampling completed. Output saved at:", output_path)

# Define the paths to your rasters
lidarHAG_path = output_path

# Open the datasets
lidarHAG_ds = gdal.Open(lidarHAG_path, gdal.GA_ReadOnly)
pcl_ds = gdal.Open(pcl_path, gdal.GA_ReadOnly)

# Function to extract raster details
def get_raster_details(dataset):
    geotransform = dataset.GetGeoTransform()
    projection = dataset.GetProjection()
    cols = dataset.RasterXSize
    rows = dataset.RasterYSize
    pixel_width = geotransform[1]
    pixel_height = geotransform[5]
    
    return {
        "cols": cols,
        "rows": rows,
        "pixel_width": pixel_width,
        "pixel_height": pixel_height,
        "projection": projection
    }

# Get details for both datasets
lidarHAG_details = get_raster_details(lidarHAG_ds)
pcl_details = get_raster_details(pcl_ds)

# Print the details
print("LIDAR HAG Raster Details:")
print("Columns:", lidarHAG_details['cols'])
print("Rows:", lidarHAG_details['rows'])
print("Pixel Width:", lidarHAG_details['pixel_width'])
print("Pixel Height:", lidarHAG_details['pixel_height'])
print("Projection:", lidarHAG_details['projection'])

print("\nPCL Raster Details:")
print("Columns:", pcl_details['cols'])
print("Rows:", pcl_details['rows'])
print("Pixel Width:", pcl_details['pixel_width'])
print("Pixel Height:", pcl_details['pixel_height'])
print("Projection:", pcl_details['projection'])

# Close datasets
lidarHAG_ds = None
pcl_ds = None
print("DONE!!!")

In [1]:
# THIS MAKES A LIST OF LAT LONG
import rasterio
from rasterio.features import geometry_mask
from shapely.geometry import Point, box
from geopandas import GeoDataFrame
import numpy as np

# Load the GeoTIFF file
file_path = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\Input\pcl_west_wgs_CO_3.tif"
with rasterio.open(file_path) as src:
    # Extract the bounds of the raster
    bounds = src.bounds
    crs = src.crs

# Create a box from the bounds
rect = box(bounds.left, bounds.bottom, bounds.right, bounds.top)

# Apply a negative buffer to contract the boundary of the rectangle
buffered_rect = rect.buffer(-0.00001)  # Change 1000 to your desired buffer distance in units of the CRS

# Check if the buffered rectangle is empty (can happen with large negative buffers)
if buffered_rect.is_empty:
    raise ValueError("Buffer size is too large")

# Function to generate random points within a geometry
def generate_random_points(geometry, num_points):
    points = []
    min_x, min_y, max_x, max_y = geometry.bounds
    while len(points) < num_points:
        random_point = Point(np.random.uniform(min_x, max_x), np.random.uniform(min_y, max_y))
        if random_point.within(geometry):
            points.append(random_point)
    return points

# Generate random points within the buffered rectangle
random_points = generate_random_points(buffered_rect, 20000)

# Convert these points to a GeoDataFrame
gdf_points = GeoDataFrame(geometry=random_points, crs=crs)

# Convert geometries from the CRS to WGS84 for latitude and longitude
gdf_points_wgs84 = gdf_points.to_crs(epsg=4326)

# Extract the latitude and longitude
lat_long = gdf_points_wgs84.geometry.apply(lambda geom: (geom.y, geom.x)).tolist()

# # Print the latitude and longitude coordinates
# for lat, lon in lat_long:
#     print(f"Latitude: {lat}, Longitude: {lon}")
print("done")

done


In [2]:
# 
import rasterio
from rasterio.windows import Window

# Paths to the raster file
resampled_PCL_path = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\Input\pcl_west_wgs_CO_3.tif"
resampled_lidar_path = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\Input\Resampled_LIDAR_GEDI_CO_11.tif"

# Size of the chip around the point (in pixels)
chip_size = 64  # creates a 200x200 pixels chip (100 pixels on each side of the point)

for i in range(len(random_points)):
    try:
        # Define the coordinates of the point (replace these with your actual coordinates)
        x_coord = lat_long[i][1] 
        y_coord = lat_long[i][0] 
        
        # Open the resampled LIDAR raster
        with rasterio.open(resampled_PCL_path) as lidar:
            # Convert the geographic coordinates to pixel coordinates
            col, row = lidar.index(x_coord, y_coord)
            
            # Calculate the window
            window = Window(col - chip_size, row - chip_size, 2 * chip_size, 2 * chip_size)
            
            # Read the data within the window
            chip_data = lidar.read(window=window)
            
            # Prepare metadata for the chip raster
            out_meta = lidar.meta.copy()
            out_meta.update({
                "driver": "GTiff",
                "height": chip_data.shape[1],
                "width": chip_data.shape[2],
                "transform": lidar.window_transform(window)
            })
        
            # Save the chip data to a new file
            chip_output_path = f"C:\\Users\\smdur\\OneDrive\\Desktop\\GLOBALPCL\\CNNPCLDEMO\\labels3\\PCL_Chip_{i}.tif"
            #with rasterio.open(chip_output_path, "w", **out_meta) as dest:
            #    dest.write(chip_data)
            #print(chip_data.shape)
            try:
                if chip_data.shape == (1,2 * chip_size,2 * chip_size) and not np.allclose(chip_data, 0):
                    with rasterio.open(chip_output_path, "w", **out_meta) as dest:
                        dest.write(chip_data)
                else:
                    print(f"Skipping chip {i} because its shape is not 200x200.")
            except Exception as e:
                print(f"Error occurred while saving chip {i}: {e}")
        
        print("Image chip created and saved to:", chip_output_path)
        
        # Open the resampled LIDAR raster
        with rasterio.open(resampled_lidar_path) as lidar:
            # Convert the geographic coordinates to pixel coordinates
            col, row = lidar.index(x_coord, y_coord)
            
            # Calculate the window
            window = Window(col - chip_size, row - chip_size, 2 * chip_size, 2 * chip_size)
            
            # Read the data within the window
            chip_data = lidar.read(window=window)
            
            # Prepare metadata for the chip raster
            out_meta = lidar.meta.copy()
            out_meta.update({
                "driver": "GTiff",
                "height": chip_data.shape[1],
                "width": chip_data.shape[2],
                "transform": lidar.window_transform(window)
            })
        
            # Save the chip data to a new file
            chip_output_path = f"C:\\Users\\smdur\\OneDrive\\Desktop\\GLOBALPCL\\CNNPCLDEMO\\inputfeatures3\\LIDAR_Chip_{i}.tif"
            #with rasterio.open(chip_output_path, "w", **out_meta) as dest:
            #    dest.write(chip_data)
            try:
                if chip_data.shape == (1,2 * chip_size,2 * chip_size) and not np.isnan(chip_data).all():
                    with rasterio.open(chip_output_path, "w", **out_meta) as dest:
                        dest.write(chip_data)
                else:
                    print(f"Skipping chip {i} because its shape is not 200x200.")
            except Exception as e:
                print(f"Error occurred while saving chip {i}: {e}")
        
        
        print("Image chip created and saved to:", chip_output_path)
    except:
        continue

Skipping chip 0 because its shape is not 200x200.
Image chip created and saved to: C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\labels3\PCL_Chip_0.tif
Skipping chip 0 because its shape is not 200x200.
Image chip created and saved to: C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\inputfeatures3\LIDAR_Chip_0.tif
Image chip created and saved to: C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\labels3\PCL_Chip_1.tif
Image chip created and saved to: C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\inputfeatures3\LIDAR_Chip_1.tif
Skipping chip 2 because its shape is not 200x200.
Image chip created and saved to: C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\labels3\PCL_Chip_2.tif
Skipping chip 2 because its shape is not 200x200.
Image chip created and saved to: C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\inputfeatures3\LIDAR_Chip_2.tif
Image chip created and saved to: C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\labels3\PCL_Chip_3.tif
Image chip

In [4]:
import os
import rasterio
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout

# Paths to datasets
featurepath1 = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\inputfeatures4\hag"
featurepath2 = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\inputfeatures4\dem"

labelspath = r"C:\Users\smdur\OneDrive\Desktop\GLOBALPCL\CNNPCLDEMO\labels3"

# Function to load GeoTIFF images as numpy arrays
def load_geotiff(path):
    with rasterio.open(path) as src:
        return src.read(1)

# Load datasets
feature_images = [load_geotiff(os.path.join(featurepath, f)) for f in os.listdir(featurepath) if f.endswith('.tif')]
label_images = [load_geotiff(os.path.join(labelspath, f)) for f in os.listdir(labelspath) if f.endswith('.tif')]

# Convert lists to numpy arrays
feature_images = np.array(feature_images).astype('float32')
label_images = np.array(label_images).astype('float32')

# Determine maximum value in feature images to normalize correctly
feature_max = feature_images.max()
print(feature_max)
# Normalize to the range [0, 1]
feature_images /= feature_max
label_images /= 100  # Assuming label images range from 0 to 100

# Reshape for CNN input
feature_images = np.expand_dims(feature_images, axis=-1)
label_images = np.expand_dims(label_images, axis=-1)

# Define the CNN model
# model = Sequential([
#     Conv2D(16, (3, 3), activation='relu', input_shape=(200, 200, 1)),
#     MaxPooling2D((2, 2)),
#     Conv2D(32, (3, 3), activation='relu'),
#     MaxPooling2D((2, 2)),
#     Conv2D(64, (3, 3), activation='relu'),
#     Flatten(),
#     Dense(1024, activation='relu'),
#     Dense(200 * 200, activation='sigmoid'),  # Assuming regression-like task
#     tf.keras.layers.Reshape((200, 200, 1))
# ])


model = Sequential([
    Conv2D(16, (3, 3), activation='relu', input_shape=(128, 128, 1)),
    MaxPooling2D((2, 2)),
    Dropout(0.25),  # Dropout 25% of the nodes
    Conv2D(32, (3, 3), activation='relu'),
    MaxPooling2D((2, 2)),
    Dropout(0.25),  # Dropout 25% of the nodes
    Conv2D(64, (3, 3), activation='relu'),
    Flatten(),
    Dropout(0.5),  # Higher dropout for fully connected layer
    #Dense(1024, activation='relu'),
    Dense(128 * 128, activation='sigmoid'),  # Assuming regression-like task
    tf.keras.layers.Reshape((128, 128, 1))
])



# Compile the model
model.compile(optimizer='adam', loss='mse')  

# Train the model
model.fit(feature_images, label_images, batch_size=64, epochs=10, validation_split=0.1)


36.0
Epoch 1/10
178/178 [==============================] - 620s 3s/step - loss: 0.0488 - val_loss: 0.0545
Epoch 2/10
178/178 [==============================] - 618s 3s/step - loss: 0.0393 - val_loss: 0.0412
Epoch 3/10
178/178 [==============================] - 613s 3s/step - loss: 0.0370 - val_loss: 0.0408
Epoch 4/10
178/178 [==============================] - 615s 3s/step - loss: 0.0357 - val_loss: 0.0398
Epoch 5/10
178/178 [==============================] - 611s 3s/step - loss: 0.0345 - val_loss: 0.0383
Epoch 6/10
178/178 [==============================] - 627s 4s/step - loss: 0.0338 - val_loss: 0.0365
Epoch 7/10
178/178 [==============================] - 631s 4s/step - loss: 0.0324 - val_loss: 0.0356
Epoch 8/10
178/178 [==============================] - 630s 4s/step - loss: 0.0314 - val_loss: 0.0365
Epoch 9/10
178/178 [==============================] - 632s 4s/step - loss: 0.0297 - val_loss: 0.0357
Epoch 10/10
178/178 [==============================] - 638s 4s/step - loss: 0.0282 - v

In [6]:
model.save('C:\\Users\\smdur\\OneDrive\\Desktop\\GLOBALPCL\\SavedModels\\model_4_29.h5')  # Saves the model in HDF5 format


C:\Users\smdur\anaconda3\envs\globalpcl\lib\site-packages\keras\src\engine\training.py:3000: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


In [7]:
# this ensures all tiles are widthtile by heighttile
import os
from itertools import product
import rasterio as rio
from rasterio import windows

in_path = 'C:\\Users\\smdur\\OneDrive\\Desktop\\GLOBALPCL\\CNNPCLDEMO\\Input\\'
input_filename = 'Resampled_LIDAR_GEDI_CO_11.tif'
out_path = 'C:\\Users\\smdur\\OneDrive\\Desktop\\GLOBALPCL\\HAGTiles3\\'
output_filename = 'tile_{}-{}.tif'
widthtile = 128
heighttile = 128

def get_tiles(ds, width=widthtile, height=heighttile):
    nols, nrows = ds.meta['width'], ds.meta['height']
    #offsets = product(range(0, nols, width), range(0, nrows, height))
    offsets = product(range(0, nols, 1000), range(0, nrows, 1000))

    big_window = windows.Window(col_off=0, row_off=0, width=nols, height=nrows)
    for col_off, row_off in offsets:
        window = windows.Window(col_off=col_off, row_off=row_off, width=width, height=height).intersection(big_window)
        transform = windows.transform(window, ds.transform)
        yield window, transform

with rio.open(os.path.join(in_path, input_filename)) as inds:
    tile_width, tile_height = widthtile, heighttile
    nodata = inds.nodata  # Get the NoData value from the dataset
    meta = inds.meta.copy()

    for window, transform in get_tiles(inds):
        if window.width == tile_width and window.height == tile_height:  # Check if the tile dimensions are as expected
            data = inds.read(window=window)
            if nodata is not None:
                # Modified check for NoData to include tolerance for floating-point rasters
                valid_data_mask = (data != nodata)
            else:
                # If NoData value is not set, consider all data as valid
                valid_data_mask = (data == data)

            if valid_data_mask.any():  # Check if there's any valid data within the tile
                meta['transform'] = transform
                meta['width'], meta['height'] = window.width, window.height
                outpath = os.path.join(out_path, output_filename.format(int(window.col_off), int(window.row_off)))
                with rio.open(outpath, 'w', **meta) as outds:
                    outds.write(data)

print("Done")


Done


In [11]:
feature_max

36.0

In [9]:
import os
import rasterio
import numpy as np
import tensorflow as tf

tilename = '0-0'
input_image_path = f"C:\\Users\\smdur\\OneDrive\\Desktop\\GLOBALPCL\\HAGTiles3\\tile_{tilename}.tif"

# Ensure 'feature_max' is correctly defined (use a known value or calculate it)
#feature_max = 100  # Example value, adjust based on actual maximum height from your data

def load_and_preprocess_image(path):
    with rasterio.open(path) as src:
        image = src.read(1)
    print("Max value in image before normalization:", np.max(image))  # Debug print
    image = np.array(image).astype('float32') / feature_max
    image = np.expand_dims(image, axis=-1)
    image = np.expand_dims(image, axis=0)
    return image

input_image = load_and_preprocess_image(input_image_path)
predicted_image = model.predict(input_image)
predicted_image = np.squeeze(predicted_image)

# Debug print to check if all outputs are the same
print("Unique values in predicted output:", np.unique(predicted_image))

predicted_image *= 100

output_image_path = f"C:\\Users\\smdur\\OneDrive\\Desktop\\GLOBALPCL\\testexample\\predictions\\predicted_tile_{tilename}.tif"
with rasterio.open(input_image_path) as src:
    profile = src.profile

with rasterio.open(output_image_path, 'w', **profile) as dst:
    dst.write(predicted_image.astype(rasterio.uint8), 1)

print("Done")


Max value in image before normalization: 20
1/1 [==============================] - 0s 162ms/step
Unique values in predicted output: [0.04166228 0.04320964 0.04552928 ... 0.49288437 0.4955583  0.5018494 ]
Done
